# Statistical birds eye view of the contents in an AiiDAdb

This is the first of two deliverable for the SiSc-Lab2020 project.

Authors = 

Supervisors: Jens Bröder, Dr. Daniel Wortmann, Johannes Wasmer, Prof. Dr. Stefan Blügel.

# Instructions by supervisors

## Jens

You have to implement this notebook.

In the end only text (markdown) cells and output results of code cells should be seen if one hides the code cells (hide_code extension).

That can easily exported into a nice pdf file (google it, probably will find sth with `nbconvert`).

Also the amount of python code in this notebook should be minimal.

Rather, export the functions you use to python file(s) and import them here (hide complexity).

Optional dump query results in a file, from which results will be reread for speed, i.e cache results.

## Johannes



After talking with Jens about it, here are some additional thoughts on the code structure and implementation, for both deliverables.

The **primary** goal is of course that the code should work, produce nice output (and helpful error messages), obviously.

The **secondary** goal is speed. How long do you expect your code to run on a dataset of a given size? Are there multiple paths to a goal, but with differing performance?

You can break the runtime down into several steps: data acquisition, data transformation (or preprocessing), data analysis, data visualization. In this project, we will rename/replace these steps to: **querying, de-/serialization, analysis=visualization**.

**Querying the database.** Performance considerations:
- Performance measurement: use the magics `%time` and `%timeit`.
- Query evaluations: queries (in general) use 'lazy evaluation'.
  - *Query building* methods build the query but do not execute it. These are chainable methods like `append()`, `get_outgoing()`, etc.
  - *Query execution* methods send the query to the database to be evaluated. There are two kinds:
    - non-iterator methods: e.g. `all()`, `first()`, etc. These return a result `list`: all items are loaded into memory.
    - iterator methods: e.g. `iterall()`, `iterdict()`. These return a result `Generator`: only one item at a time is loaded into memory.
    
**De-/serialization**, i.e. writing and reading it to/from a file. *Keep in mind: if you come to the conclusion this is unnecessary, then justify it!* Considerations:
- Necessity: we assume 'yes'. So you need serialization/deserialization routine(s).
- Code design: we recommend to write a serializer that moves *all* data needed from aiida to file (perform query & serialization). Then the visualization methods are decoupled from aiida and load data from that file. Advantages: a) only needs to be called when data in database changed, b) similar queries for different visualizations can be performed only once. One design option is this:
  ```python
  serialize = sisclab.Serializer(profile)
  serialize.to_file(filepath)
  visualize = sisclab.Visualizer(filepath)
  visualize.histogram(cumulative=True, plot_options)
  # plots histogram
  ```
- Serialization format: there are two practical options (maybe more):
  - `dict`: tree-like. JSON format. One `dict` per file. choose key-value (nested?) based on use-case. in general, `uuid` is a good key.
  - `pandas.Dataframe`: could be preferrable in some cases.
- Serialization location:
  - one file or several files?
  - we recommend to de/serialize from/to `sisclab/data/` folder. It is included in the project's `.gitignore` file, so nothing in it gets committed to/from git (git is for code, not for data; the code generates the data).
- Transformation:
  - if needed, decide where to put needed data transformations (before serialization or after deserialization) to minimize them.
- Deserialization: 
  - a class (as above) might help to define the deserialization format only once for all visualization methods.
  

**Visualization**:
- Prefer `bokeh` to `matplotlib` or other libs wherever possible, unless you have a good justification.
- In `D1`, static plots are okay, interactive plots are a bonus.
- Lists results (when plot is overkill) will look nicer in a notebook if they are a `pandas.Series` or `pandas.Dataframes`.
- Think about function signatures. Can you generalize them to make a nice interface? For example, a signature for SubtaskD1.c might look like this:
  ```python
  def node_type_summary(user_list : list = [], node_basetype : Node = Data,
                        chart_type : bokeh.chart_type = bokeh.pie_chart, plot : bool = True):
    """
    :param user_list: list of users. empty list = all users = default.
    :param node_basetype: subdivides chart into subtypes. Valid base type examples: ProcessNode, CalculationNode, WorkflowNode, Data, ArrayData.
    :param chart_type: bokeh visualization type. pie chart = default.
    :param plot: True: show plot, don't return data. False: don't plot, return data.
    :return: stats: a dictionary {node_subtype : node_count}, insertion-order sorted in descending order.
    :rtype: dict.
    """
  ```


# Imports

In [1]:
# magics:
# # autoreload imports. 
# # intent: if i change sth in import, i don't have to restart kernel. enable only for development.
%load_ext autoreload
%autoreload 2
# # choose matplotlib backend. backend 'notebook' allows interactive plots if your env allows it.
%matplotlib notebook


In [2]:
# python imports:
from collections import Counter
import time
#from pprint import pprint

In [3]:
#%pylab inline
#figuresize=(18, 4)
from collections import Counter
from math import pi
import pandas as pd
from bokeh.io import output_file,output_notebook, show
from bokeh.layouts import column
from bokeh.palettes import Category20c
from bokeh.plotting import figure
from bokeh.transform import cumsum
from bokeh.models import Legend,LegendItem

In [4]:
# aiida imports:
from aiida import load_profile
profile = load_profile()

# ggf add futher imports
from aiida.orm import QueryBuilder as QB
from aiida.orm import Node, User, CalcJobNode, Computer, Code
from aiida.plugins import DataFactory

from aiida.common.constants import elements as PeriodicTableElements

In [12]:
# project imports:
#import helpers
#from ..helpers import *
# equivalent ('.' is the sisc_lab directory):
# from . import helpers
# alternative:
# from .helpers import print_bold
# from .helpers import * ('*' import everything; use of '*' is considered bad style)

In [13]:
from aiida_jutools.sisc_lab import helpers

In [ ]:
import bokeh
from bokeh.io import output_notebook

In [ ]:
output_notebook()

In [14]:
# (example:)
helpers.print_bold(f"This notebook/dashboard will visualize the contents from the database of profile {profile.name}")

This notebook/dashboard will visualize the contents from the database of profile broeder_work


# SubtaskD1.a: Node information

Task:

In [15]:
# query for all nodes
print('Information on nodes in the DB: \n')
now = time.strftime("%c")
print('last executed on {}'.format(now))
q = QB()
q.append(Node, project=['id', 'ctime', 'mtime', 'node_type'], tag='node')
q.append(User, with_node='node', project='email')
# TODO: execute query here
t = time.time()
elapsed = time.time() - t
res = q.all()
totalnodes = len(res)
print("Total number of nodes in the database: {} (retrieved in {} s.)".format(totalnodes, elapsed))

Information on nodes in the DB: 

last executed on Fri Jan  8 07:44:33 2021
Total number of nodes in the database: 137670 (retrieved in 9.608268737792969e-05 s.)


# SubtaskD1.b: Users

Task: print out a list of Users and how many nodes belong to them

for example

```
Users:
- j.broeder@fz-juelich.de created 182 nodes
- tests@aiida.mail created 104 nodes
```

In [16]:
users = Counter([r[4] for r in res])
print("Users:")
for count, email in sorted((v, k) for k, v in users.items())[::-1]:
    print("* {} created {} nodes".format(email, count))

Users:
* j.broeder@fz-juelich.de created 137670 nodes


# SubtaskD1.c: Node types

Task: plot node information in two pie chart plots

One showing what data nodes there (with their lowest class names(node_type)) I.e Dict, K-pointsData, CifData, FleurinpData...

And one chart showning the process nodes, (with their lowest class names(process_type) i.e CalcjobNodes: FleurCalcjob, FleurinputgenCalcjob, ...

WorkChain nodes: FleurSCFWorkchain, FleurBandDosWorkchain, ..., calcfunctions, and workfunction nodes are fine to not show the lowest class names


In [17]:
#node types
types = Counter([r[3] for r in res])
print("Node types:")

for count, typestring in sorted((v, k) for k, v in types.items())[::-1]:
    print("* {}: {} nodes".format(typestring, count))

Node types:
* data.dict.Dict.: 31136 nodes
* process.workflow.workfunction.WorkFunctionNode.: 20087 nodes
* process.calculation.calcjob.CalcJobNode.: 16298 nodes
* data.fleur.fleurinp.FleurinpData.: 15709 nodes
* data.remote.RemoteData.: 15135 nodes
* data.folder.FolderData.: 13948 nodes
* data.structure.StructureData.: 11324 nodes
* process.workflow.workchain.WorkChainNode.: 7676 nodes
* data.float.Float.: 5351 nodes
* data.int.Int.: 697 nodes
* data.str.Str.: 148 nodes
* data.cif.CifData.: 98 nodes
* data.Data.: 41 nodes
* data.code.Code.: 22 nodes


In [18]:
#split data nodes and process nodes
labelst_1,labelst_2=[],[]
sizest_1,sizest_2=[],[]
#labelst = [label.split('.')[0]=='data' for label in types.keys()]
#sizest = [nnodes for nnodes in types.values()]
for k,v in types.items():
    if k.split('.')[0]=='data':
        labelst_1.append(k.split('.')[-2])
        sizest_1.append(v)
    elif k.split('.')[0]=='process':
        labelst_2.append(k.split('.')[-2])
        sizest_2.append(v)
        
#plot data nodes
#output_file("pie.html")
output_notebook()
x = dict(zip(labelst_1,sizest_1)) 
data=pd.DataFrame.from_dict(dict(x),orient='index').reset_index().rename(index=str,columns={0:'value','index':'data_nodes'})
data['angle'] = data['value']/sum(x.values()) * 2*pi
data['color'] = Category20c[len(x)]
p = figure(plot_height=350, title="Data Nodes", toolbar_location=None,
           tools="hover", tooltips="@data_nodes: @value")
p.wedge(x=0, y=1, radius=0.4,
        start_angle=cumsum('angle', include_zero=True), end_angle=cumsum('angle'),
        line_color="white", fill_color='color', legend_field='data_nodes', source=data)
p.axis.axis_label=None
p.axis.visible=False
p.grid.grid_line_color = None 
#show(p)                        

#plot process node

x1 = dict(zip(labelst_2,sizest_2)) 
data=pd.DataFrame.from_dict(dict(x1),orient='index').reset_index().rename(index=str,columns={0:'value','index':'process_nodes'})
data['angle'] = data['value']/sum(list(x1.values())) * 2*pi
data['color'] = Category20c[len(x1)]
p1 = figure(plot_height=350, title="Process Nodes", toolbar_location=None,
           tools="hover", tooltips="@process_nodes: @value")
p1.wedge(x=0, y=1, radius=0.4,
        start_angle=cumsum('angle', include_zero=True), end_angle=cumsum('angle'),
        line_color="white", fill_color='color', legend_field='process_nodes', source=data)
p1.axis.axis_label=None
p1.axis.visible=False
p1.grid.grid_line_color = None 
show(column(p,p1))


Loading BokehJS ...

# SubtaskD1.d: Histogram

Task: Cumulative Histogram/ or line plot by ctime & mtime of all nodes over time

In [19]:
# line plot by ctime & mtime

ctimes = sorted(r[1] for r in res)
mtimes = sorted(r[2] for r in res)
num_nodes_integrated = range(len(ctimes))
df = pd.DataFrame({'A':ctimes,"B":mtimes})

#print(df.head())
#df = pd.DataFrame({'A':np.random.randn(100).cumsum(),"B":np.random.randn(100).cumsum()})

#plot multiline
p = figure(plot_width=900, plot_height=300, x_axis_type='datetime')
r=p.multi_line([df['A'], df['B']],  
               [df.index, df.index],   
               color=["firebrick", "navy"],   
               alpha=[0.8, 0.6],     
               line_width=[2,1],     
              )

legend=Legend(items=[
    LegendItem(label="ctime",renderers=[r],index=0),
    LegendItem(label="mtime",renderers=[r],index=1),
])
p.add_layout(legend)
p.xaxis.axis_label = 'Date'
p.yaxis.axis_label = 'Number of nodes'

show(p)

# SubtaskD1.e: Codes

Task: List Code names, sorted by by how many calcjobs where run with each

In [20]:
codes = Code.objects.all()
result = {code.label : len(code.get_outgoing(node_class=CalcJobNode).all_nodes()) for code in codes}
result_df=pd.Series(result).sort_values(ascending=False)
result_df

inpgen                   7257
inpgen_max_2             2442
fleur_mpi_max_1.3_dev    1611
fleur_v0.28               749
fleur_max_1.3_dev         563
fleur_mpi_max_2           241
fleur_dev_mpi             203
voro                       14
kkr1                       11
fleur_max_2                 4
fleur_mac_3_mpi             0
inpgen_v0.28                0
kkrimp                      0
inpgen_mac                  0
inpgen_iff_0.28             0
fleur_iff_0.28              0
fleur_mpi_v0.28             0
fleur_dev_mpi_booster       0
dtype: int64

# SubtaskD1.f: Groups

Task: List all group names with how many nodes they contain (verdi group list -C) (exclude import and export groups)

In [21]:
def ListGroup(Group : list, exclude: list=[]):
    """ return the group names and nodes they contain
    
    :the list of all groups
    :the list of all excluded groups name
    """
    print('{:<52}{:6}'.format('Group names:','sizes:'))
    for a in Group:
        flag=0
        type = a[0].type_string
        for ex in exclude:
            if ex in type:
                flag=1
        if(flag):
            continue     
        else:
            ## the line below contains all the properties
            ##print(a[0].label,' ',a[0].user,' ',a[0].type_string,' ',a[0].description)

            print('{:<50}|{:5}'.format(a[0].label,len(a[0].nodes)))

In [22]:
load_profile()
#!verdi group list --all
from aiida.orm import QueryBuilder
from aiida.orm import load_node, Node, Group, Computer, User, CalcJobNode, Code, StructureData

qb = QueryBuilder()
qb.append(Group)
#print(qb.all())

group = qb.all()
ListGroup(group,exclude=['export','import'])

Group names:                                        sizes:
codes                                             |   18
delta_parameters_gustav                           |   71
delta_structures_gustav                           |   71
fusion_materials                                  |   79
delta_structures_gustav_rev                       |   66
delta_parameters_gustav_rev                       |   66
stable_binary_metals_from_materialsproject        | 5058
fleur_initial_cls_finished                        |    7
delta_parameters_gutstav_soc                      |   71
fusion_strucs_refinded                            |   23
Verdi autogroup on 2017-07-10 11:15:44            |    1
Verdi autogroup on 2017-07-10 17:40:53            |    1
Verdi autogroup on 2018-06-21 08:38:38            |   15
Verdi autogroup on 2018-06-21 08:44:23            |   15
Verdi autogroup on 2018-06-21 08:46:33            |   15


# SubtaskD1.g: Structures

Task: Further analyze what structures are in the DB

Number of structureData node versus how many atoms they contain. 

here interactive with bokeh hover tool showing the structure formula and uuid

Number of StructureData nodes versus elements bokeh bar chart, since there are over 
100 elements in the periodic table you can split it over several plots, or just use the charge number as in 
'example/element_content.png' but then make it interactive that once one hovers 
with the mouse over a bar it tells you what element it is and how many structures there are containing this element-

In [27]:
from aiida.orm import QueryBuilder
from aiida.orm import load_node, Node, Group, Computer, User, CalcJobNode, Code, StructureData
from aiida_jutools.sisc_lab.HelperPackage import DataProcessing
from aiida_jutools.sisc_lab.HelperPackage.DataProcessing.DataVisu import StrucDataForm

def NumStructureNode():
    #### return the pd.DataFrame including elements and number of each element
    import pandas as pd
    StrucList = []
    qb = QueryBuilder()
    qb.append(StructureData)
    print('number of StructureData Nodes:',qb.count())
    qb.count()

    for struc, in qb.all()[:]:
        form = struc.get_formula()
        struct = StrucDataForm(form)
        StrucList = StrucList+ [struct.FormAnalyse()]
    return pd.DataFrame(StrucList).fillna(0)

def ShowElements(Data):
    from bokeh.io import output_file, show
    from bokeh.models import ColumnDataSource,HoverTool
    from bokeh.plotting import figure
    from bokeh.io import output_notebook
    from bokeh.palettes import inferno

    output_file("ShowingElements.html")
    #data = NumStructureNode()
    data = Data
    elements = list(data.columns)
    counts = list(data.astype(bool).sum(axis=0))
    #print(counts)
    #print(elements)
    
    source = ColumnDataSource(data=dict(elements=elements, counts=counts,color=inferno(len(elements))))
    
    TOOLTIPS = [
    ("element", "@elements"),
    ("(x,y)", "($x, $y)"),
    ("Number of Structures containing this element", "@counts"),
    ]

    p = figure( y_range=elements,x_range=(0,500), plot_width=800, plot_height=800, title="Elements Counts",tools = [HoverTool(mode='hline')], tooltips=TOOLTIPS)
    #print('step figure done')
    p.hbar(y="elements", right="counts", height=0.5, left=0, color='color',  source=source)
    #print('step hbar done')
    
    output_notebook()
    p.xgrid.grid_line_color = None
    #p.legend = False
    show(p)
    
    
def ShowFormula(Data):
    from bokeh.io import output_file, show
    from bokeh.models import ColumnDataSource,HoverTool
    from bokeh.plotting import figure
    from bokeh.io import output_notebook
    from bokeh.palettes import inferno

    data = Data
    elements = list(data.keys())
    counts = list(len(data[key])/2 for key in data.keys())
    formulas = list(data[key] for key in data.keys())

    length = len(elements)
    source = ColumnDataSource(data=dict(elements=elements, counts=counts,formulas=formulas,color=inferno(length)))
    
    TOOLTIPS = [
    ("Number of Atoms", "@elements"),
    ("(x,y)", "($x, $y)"),
    ("Number of Nodes", "@counts"),
    ("id and formula", "@formulas"),
    ]

    p = figure( y_range=(0,160),x_range=(0,1000), plot_width=800, plot_height=800, title="Atoms Count",tools = [HoverTool(mode='hline')], tooltips=TOOLTIPS)
    #print('step figure done')
    p.hbar(y="elements", right="counts", height=0.5, left=0, color='color',  source=source)
    #print('step hbar done')
    
    output_notebook()
    p.xgrid.grid_line_color = None
    #p.legend = False
    show(p)
    
def GetFormulaDict():
    ## may be not necessary, return the formulas and nodes containing this formula
    import numpy as np
    from aiida.orm import QueryBuilder,StructureData
    qb = QueryBuilder()
    qb.append(StructureData)
    Mydict = qb.all()
    Mydict = np.ravel(Mydict)

    Newdict = {}
    for dict in Mydict:
        if dict.get_formula in Newdict.keys():
            Newdict[dict.get_formula()].append(dict.uuid)
        else:
            Newdict[dict.get_formula()] = [dict.uuid]
    return Newdict

def AtomsNumNodes():
    from aiida.orm import QueryBuilder,StructureData
    import numpy as np
    qb = QueryBuilder()
    qb.append(StructureData)
    StructDatas = qb.all()
    Newdict = {}
    
    for data, in StructDatas:
        CompositionDict = data.get_composition()
        NumAtom = np.sum(list(CompositionDict.values()))
        if NumAtom in Newdict.keys():
            Newdict[NumAtom].append(data.uuid)
            Newdict[NumAtom].append(data.get_formula())
        else:
            Newdict[NumAtom] = [data.uuid,data.get_formula()]
    return Newdict

In [28]:
dic = AtomsNumNodes()
ShowFormula(dic)

Loading BokehJS ...

In [29]:
data = NumStructureNode()
ShowElements(data)

number of StructureData Nodes: 11324


Loading BokehJS ...

In [31]:
# initialize the Structure data
from aiida.orm import QueryBuilder
from aiida.orm import load_node, Node, Group, Computer, User, CalcJobNode, Code, StructureData
from aiida_jutools.sisc_lab.HelperPackage import DataProcessing
from aiida_jutools.sisc_lab.HelperPackage.DataProcessing.DataVisu import StrucDataForm


qb = QueryBuilder()
qb.append(StructureData)

structures = qb.all()

for structure in structures[:]:
    formula = structure[0].get_formula()
    struct = StrucDataForm(formula)
    structure[0].get_composition()
    print(struct.FormAnalyse())

{'O': '112', 'W': '40'}
{'O': '58', 'W': '20'}
{'O': '49', 'W': '18'}
{'O': '58', 'W': '20'}
{'W': '1'}
{'Be': '2'}
{'Be': '4'}
{'Be': '2'}
{'W': '2'}
{'W': '1'}
{'W': '1'}
{'W': '1'}
{'W': '1'}
{'W': '1'}
{'W': '1'}
{'W': '1'}
{'W': '1'}
{'W': '1'}
{'W': '1'}
{'W': '1'}
{'Be': '2'}
{'Be': '2'}
{'Be': '2'}
{'Be': '2'}
{'Be': '2'}
{'Be': '2'}
{'Be': '2'}
{'Be': '2'}
{'W': '2'}
{'W': '2'}
{'Be': '2'}
{'Rn': '1'}
{'Rn': '1'}
{'N': '8'}
{'N': '8'}
{'I': '8'}
{'Bi': '2'}
{'Bi': '2'}
{'Bi': '2'}
{'Si': '4'}
{'Be': '16', 'W': '8'}
{'Be': '16', 'W': '8'}
{'Be': '4'}
{'Be': '16', 'W': '8'}
{'Be': '16', 'W': '8'}
{'Be': '16', 'W': '8'}
{'Be': '352', 'W': '16'}
{'Be': '352', 'W': '16'}
{'Be': '16', 'W': '8'}
{'Be': '16', 'W': '8'}
{'Be': '352', 'W': '16'}
{'Be': '16', 'W': '8'}
{'Be': '16'}
{'Be': '24'}
{'Be': '4'}
{'Be': '54'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '4'}
{'Be': '16'}
{'W': '1'}
{'W': '1'}
{'Be': '408', 'Ti': '48'}
{'Be': '24', 'Ti': '

{'O': '12', 'W': '4'}
{'O': '12', 'W': '11'}
{'O': '47', 'W': '17'}
{'O': '12', 'W': '11'}
{'O': '47', 'W': '17'}
{'O': '84', 'W': '32'}
{'O': '24', 'W': '8'}
{'O': '47', 'W': '17'}
{'O': '47', 'W': '17'}
{'O': '24', 'W': '8'}
{'O': '24', 'W': '8'}
{'O': '6', 'W': '2'}
{'O': '84', 'W': '32'}
{'O': '84', 'W': '32'}
{'O': '112', 'W': '40'}
{'O': '84', 'W': '32'}
{'O': '112', 'W': '40'}
{'O': '112', 'W': '40'}
{'O': '24', 'W': '8'}
{'O': '47', 'W': '17'}
{'O': '58', 'W': '20'}
{'O': '112', 'W': '40'}
{'O': '24', 'W': '8'}
{'O': '24', 'W': '8'}
{'O': '112', 'W': '40'}
{'O': '112', 'W': '40'}
{'O': '24', 'W': '8'}
{'O': '112', 'W': '40'}
{'O': '112', 'W': '40'}
{'Be': '6', 'N': '4'}
{'Be': '6', 'N': '4'}
{'O': '112', 'W': '40'}
{'O': '112', 'W': '40'}
{'Be': '6', 'N': '4'}
{'O': '112', 'W': '40'}
{'Be': '6', 'N': '4'}
{'Be': '6', 'N': '4'}
{'Be': '4', 'O': '4'}
{'Be': '4', 'O': '4'}
{'Be': '4', 'O': '4'}
{'Be': '4', 'O': '4'}
{'O': '112', 'W': '40'}
{'Be': '4', 'O': '4'}
{'Be': '4', 'O': '4

{'Ru': '2'}
{'K': '1'}
{'Kr': '1'}
{'Cu': '1'}
{'N': '8'}
{'Sc': '2'}
{'Ne': '1'}
{'Nb': '1'}
{'Bi': '2'}
{'Br': '4'}
{'As': '2'}
{'Ba': '1'}
{'B': '12'}
{'Hf': '2'}
{'Be': '2'}
{'Co': '2'}
{'Tc': '2'}
{'Cl': '4'}
{'Pd': '1'}
{'W': '1'}
{'He': '2'}
{'Ni': '1'}
{'Tl': '2'}
{'Pt': '1'}
{'Ca': '1'}
{'Ir': '1'}
{'Be': '24', 'Cr': '2'}
{'Be': '8', 'Cr': '4'}
{'Be': '2'}
{'O': '24', 'W': '8'}
{'O': '58', 'W': '20'}
{'Be': '24', 'W': '2'}
{'Cr': '8'}
{'Cr': '2'}
{'O': '112', 'W': '40'}
{'O': '24', 'W': '12'}
{'O': '12', 'W': '4'}
{'O': '24', 'W': '8'}
{'O': '12', 'W': '4'}
{'O': '4', 'W': '2'}
{'Be': '2', 'O': '2'}
{'Ta': '2'}
{'Be': '4', 'O': '4'}
{'Cr': '2'}
{'Be': '4', 'O': '4'}
{'Cr': '26'}
{'Be': '24', 'Ti': '2'}
{'W': '1'}
{'Be': '9', 'N': '6'}
{'Be': '3', 'N': '2'}
{'Be': '6', 'N': '4'}
{'O': '16', 'W': '6'}
{'Cr': '4'}
{'O': '24', 'W': '8'}
{'O': '47', 'W': '17'}
{'O': '2', 'W': '6'}
{'O': '9', 'W': '3'}
{'O': '12', 'W': '4'}
{'Cr': '12'}
{'Be': '1', 'Ti': '1'}
{'Be': '34', 'Ti': '4'}

{'Be': '24'}
{'Be': '24'}
{'Be': '54'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '4'}
{'Be': '4'}
{'Be': '4'}
{'Be': '4'}
{'Be': '4'}
{'Be': '4'}
{'Be': '64', 'W': '32'}
{'Be': '4'}
{'Be': '4'}
{'Be': '4'}
{'Be': '4'}
{'Be': '4'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '1', 'Ti': '1'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '16'}
{'Be': '1', 'Ti': '1'}
{'Be': '408', 'Ti': '48'}
{'Be': '1', 'Ti': '1'}
{'Be': '1', 'Ti': '1'}
{'W': '1'}
{'Be': '1', 'Ti': '1'}
{'Be': '1', 'Ti': '1'}
{'Be': '1', 'Ti': '1'}
{'Be': '1', 'Ti': '1'}
{'Be': '1', 'Ti': '1'}
{'Be': '16', 'Ti': '8'}
{'Be': '16', 'Ti': '8'}
{'Be': '16', 'Ti': '8'}
{'Be': '

{'Be': '9', 'Ti': '3'}
{'Be': '9', 'Ti': '3'}
{'Be': '9', 'Ti': '3'}
{'Be': '9', 'Ti': '3'}
{'Be': '17', 'Ti': '2'}
{'Be': '9', 'Ti': '3'}
{'Be': '34', 'Ti': '4'}
{'Be': '9', 'Ti': '3'}
{'Be': '9', 'Ti': '3'}
{'Be': '9', 'Ti': '3'}
{'Be': '34', 'Ti': '4'}
{'Be': '9', 'Ti': '3'}
{'Be': '34', 'Ti': '4'}
{'Be': '17', 'Ti': '2'}
{'Be': '34', 'Ti': '4'}
{'Be': '34', 'Ti': '4'}
{'Be': '34', 'Ti': '4'}
{'Be': '34', 'Ti': '4'}
{'Be': '34', 'Ti': '4'}
{'Be': '17', 'Ti': '2'}
{'Be': '17', 'Ti': '2'}
{'Be': '17', 'Ti': '2'}
{'Be': '17', 'Ti': '2'}
{'Be': '17', 'Ti': '2'}
{'Be': '17', 'Ti': '2'}
{'Be': '17', 'Ti': '2'}
{'Be': '12', 'Ti': '1'}
{'Be': '12', 'Ti': '1'}
{'Be': '12', 'Ti': '1'}
{'Be': '12', 'Ti': '1'}
{'Be': '12', 'Ti': '1'}
{'Be': '12', 'Ti': '1'}
{'Be': '12', 'Ti': '1'}
{'Be': '12', 'Ti': '1'}
{'Be': '12', 'Ti': '1'}
{'Be': '12', 'Ti': '1'}
{'Be': '12', 'Ti': '1'}
{'Be': '12', 'Ti': '1'}
{'Be': '12', 'Ti': '1'}
{'Be': '12', 'Ti': '1'}
{'Be': '12', 'Ti': '1'}
{'Be': '12', 'Ti': '1'}
{

...

{'Mn': '1', 'Se': '1'}
{'Mn': '2', 'Se': '2'}
{'Mn': '4', 'Se': '8'}
{'Co': '1', 'Ti': '1'}
{'Fe': '3', 'Se': '4'}
{'Co': '4', 'Se': '8'}
{'Co': '34', 'Se': '40'}
{'Co': '3', 'Se': '4'}
{'Co': '4', 'Se': '8'}
{'Co': '2', 'Se': '2'}
{'Co': '2', 'Se': '4'}
{'Co': '9', 'Se': '8'}
{'Ni': '19', 'Se': '20'}
{'Ni': '4', 'Se': '8'}
{'Ni': '3', 'Se': '2'}
{'Ni': '2', 'Se': '2'}
{'Ni': '3', 'Se': '3'}
{'Ni': '2', 'Se': '2'}
{'Cu': '75', 'Se': '78'}
{'Cu': '29', 'Se': '19'}
{'Cu': '4', 'Se': '8'}
{'Cu': '6', 'Se': '6'}
{'Cu': '13', 'Se': '8'}
{'Cu': '2', 'Se': '2'}
{'Cu': '6', 'Se': '6'}
{'Cu': '18', 'Se': '10'}
{'Cu': '9', 'Se': '8'}
{'Cu': '9', 'Se': '5'}
{'Cu': '2', 'Se': '4'}
{'As': '10', 'Li': '27'}
{'As': '4', 'K': '5'}
{'As': '6', 'Ca': '6'}
{'As': '6', 'Ca': '2'}
{'As': '2', 'Ca': '4'}
{'As': '1', 'Sc': '1'}
{'As': '12', 'Sc': '20'}
{'As': '8', 'Sc': '12'}
{'As': '4', 'Ti': '4'}
{'As': '6', 'Ti': '8'}
{'As': '16', 'Ti': '8'}
{'As': '2', 'Ti': '6'}
{'As': '2', 'Ti': '2'}
{'As': '12', 'V': 

{'Ni': '6', 'S': '8'}
{'Ni': '4', 'S': '8'}
{'Ni': '9', 'S': '10'}
{'Ca': '1', 'Ni': '5'}
{'Ca': '2', 'Ni': '4'}
{'Ni': '5', 'Sc': '1'}
{'Ni': '4', 'Sc': '2'}
{'Ni': '12', 'Ti': '4'}
{'Ni': '9', 'Ti': '9'}
{'Ni': '2', 'Ti': '2'}
{'Sb': '2'}
{'Ni': '1', 'Ti': '1'}
{'Ni': '8', 'Ti': '6'}
{'Ni': '2', 'Ti': '2'}
{'Ni': '2', 'Ti': '2'}
{'Ni': '6', 'Ti': '6'}
{'Ni': '9', 'Ti': '9'}
{'Ni': '8', 'Ti': '16'}
{'Ni': '3', 'V': '1'}
{'Ni': '2', 'V': '1'}
{'Ni': '2', 'V': '6'}
{'Cr': '1', 'Ni': '3'}
{'Cr': '1', 'Ni': '2'}
{'Mn': '2', 'Ni': '2'}
{'Mn': '1', 'Ni': '1'}
{'Mn': '1', 'Ni': '3'}
{'Fe': '3', 'Ni': '1'}
{'Fe': '2', 'Ni': '2'}
{'Fe': '1', 'Ni': '3'}
{'Fe': '3', 'Ni': '1'}
{'Fe': '3', 'Ni': '1'}
{'Fe': '1', 'Ni': '3'}
{'Co': '3', 'Ni': '1'}
{'Co': '6', 'H': '2'}
{'Be': '1', 'Co': '1'}
{'B': '2', 'Co': '4'}
{'B': '4', 'Co': '12'}
{'B': '6', 'Co': '23'}
{'B': '4', 'Co': '4'}
{'Co': '4', 'N': '2'}
{'Co': '1', 'N': '1'}
{'Co': '21', 'O': '40'}
{'Co': '2', 'O': '4'}
{'Co': '8', 'Si': '4'}
{'Co': 

{'Al': '4', 'Ti': '2'}
{'C': '1', 'Sc': '2'}
{'Si': '4', 'Ti': '2'}
{'Si': '16', 'Ti': '20'}
{'Si': '6', 'Ti': '10'}
{'Si': '4', 'Ti': '4'}
{'Be': '26', 'Sc': '2'}
{'P': '8', 'Ti': '24'}
{'P': '6', 'Ti': '8'}
{'P': '8', 'Ti': '4'}
{'P': '12', 'Ti': '20'}
{'P': '27', 'Ti': '54'}
{'B': '2', 'Sc': '1'}
{'P': '4', 'Ti': '4'}
{'S': '24', 'Ti': '14'}
{'S': '12', 'Ti': '32'}
{'S': '8', 'Ti': '4'}
{'S': '1', 'Ti': '1'}
{'S': '2', 'Ti': '2'}
{'B': '12', 'Sc': '1'}
{'S': '12', 'Ti': '24'}
{'S': '30', 'Ti': '27'}
{'S': '2', 'Ti': '1'}
{'S': '24', 'Ti': '13'}
{'Cl': '2', 'Ti': '1'}
{'Cl': '6', 'Ti': '2'}
{'C': '40', 'Sc': '30'}
{'Cl': '32', 'Ti': '14'}
{'Cl': '12', 'Ti': '4'}
{'Cl': '6', 'Ti': '2'}
{'Cl': '6', 'Ti': '2'}
{'Mn': '2'}
{'Cl': '18', 'Ti': '6'}
{'H': '10', 'Sc': '4'}
{'H': '3', 'Sc': '1'}
{'H': '2', 'Sc': '1'}
{'Be': '5', 'Sc': '1'}
{'N': '1', 'Sc': '1'}
{'O': '19', 'Sc': '20'}
{'O': '1', 'Sc': '1'}
{'O': '15', 'Sc': '16'}
{'Al': '4', 'Sc': '2'}
{'Al': '1', 'Sc': '3'}
{'Mg': '6', 'Sc':

{'Pt': '1'}
{'Pt': '1'}
{'Pt': '1'}
{'Tl': '2'}
{'Tl': '2'}
{'Tl': '2'}
{'Tl': '2'}
{'Tl': '2'}
{'Tl': '2'}
{'Tl': '2'}
{'Ni': '1'}
{'Ni': '1'}
{'Ni': '1'}
{'Ni': '1'}
{'Ni': '1'}
{'Ni': '1'}
{'Ni': '1'}
{'He': '2'}
{'He': '2'}
{'He': '2'}
{'He': '2'}
{'He': '2'}
{'He': '2'}
{'He': '2'}
{'Pd': '1'}
{'Pd': '1'}
{'Pd': '1'}
{'Pd': '1'}
{'Pd': '1'}
{'Pd': '1'}
{'Pd': '1'}
{'Cl': '4'}
{'Cl': '4'}
{'Tc': '2'}
{'Cl': '4'}
{'Cl': '4'}
{'Cl': '4'}
{'Cl': '4'}
{'Cl': '4'}
{'Tc': '2'}
{'Tc': '2'}
{'Tc': '2'}
{'Tc': '2'}
{'Tc': '2'}
{'Tc': '2'}
{'Co': '2'}
{'Co': '2'}
{'Co': '2'}
{'Co': '2'}
{'Co': '2'}
{'Co': '2'}
{'Co': '2'}
{'Be': '2'}
{'Be': '2'}
{'Be': '2'}
{'Be': '2'}
{'Be': '2'}
{'Be': '2'}
{'Be': '2'}
{'Hf': '2'}
{'Hf': '2'}
{'Hf': '2'}
{'Hf': '2'}
{'Hf': '2'}
{'Hf': '2'}
{'Hf': '2'}
{'B': '12'}
{'B': '12'}
{'B': '12'}
{'B': '12'}
{'B': '12'}
{'B': '12'}
{'Hg': '1'}
{'Hg': '1'}
{'B': '12'}
{'Au': '1'}
{'Au': '1'}
{'Au': '1'}
{'Au': '1'}
{'Au': '1'}
{'Au': '1'}
{'Au': '1'}
{'Hg': '1'}
{'Hg

{'O': '24', 'W': '8'}
{'O': '24', 'W': '8'}
{'O': '24', 'W': '8'}
{'O': '24', 'W': '8'}
{'O': '24', 'W': '8'}
{'O': '24', 'W': '8'}
{'O': '24', 'W': '8'}
{'O': '24', 'W': '8'}
{'O': '24', 'W': '8'}
{'O': '24', 'W': '8'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}
{'Be': '192', 'Ti': '16'}


# SubtaskD1.h: Calculations

Task: more detail analysis of Calculations

`print('\n\nMore detailed analysis of Calculations \n')`

List, stacked Histogram of Calculations types and the state it ended up finished, failed, exit codes, exit messages

more detail analysis of WorkChains

`print('\n\nMore detailed analysis of WorkChains \n')`

List,  stacked Histogram for each Workchain type and the state it ended up in finished, failed, exit codes, exit messages

In [32]:
def GetCalNode():
    exit_state = []
    exit_message = []
    index = []
    exit_state_digit = []
    for node, in CalcNode:
        print(str(node.process_state))
        print(node.pk)
        #print(str(node.exit_message))
        exit_state = exit_state + [str(node.process_state)]
        exit_message = exit_message + [str(node.exit_message)]
        index = index + [node.pk]
        if node.is_finished_ok:
            exit_state_digit = exit_state_digit + [1]
        else:
            exit_state_digit = exit_state_digit + [0]
    return exit_state,exit_message,index,exit_state_digit

def ShowCalNode(exit_state,exit_message,index,exit_state_digit):
    from bokeh.io import output_file, show
    from bokeh.models import ColumnDataSource
    from bokeh.plotting import figure
    from bokeh.io import output_notebook
    from bokeh.palettes import inferno

    output_file("ShowingCal.html")

    index = index
    exit_message = exit_message
    exit_state_string = exit_state
    exit_state_digit = exit_state_digit
      
    source = ColumnDataSource(data=dict(index=index, exit_state_digit=exit_state_digit,exit_message = exit_message,exit_state_string = exit_state_string, color=inferno(len(index))))
    
    TOOLTIPS = [
    ("Exit information", "@exit_message"),
    ("(x,y)", "($x, $y)"),
    ("Node index", "@index"),
    ("Node status", "@exit_state_string"),   
    ]

    p = figure( y_range=(0,1), x_range=(0,3000), plot_width=800, plot_height=800, title="CalcNode Information", tooltips=TOOLTIPS)
    #print('step figure done')
    p.vbar(x="index", top="exit_state_digit", bottom=0, width=1, color='color',  source=source)
    #print('step hbar done')
    
    output_notebook()
    p.xgrid.grid_line_color = None
    #p.legend = False
    show(p)
    
def GetWorkflowNode(Name):
    from aiida.orm import WorkflowNode
    from aiida.orm import QueryBuilder
    qb = QueryBuilder()
    qb.append(Name)
    WNode = qb.all()

    Newdict = {}
    for node, in WNode:
        if node.is_finished_ok:
            Newdict[node.node_type+'_succeed'] = Newdict.get(node.node_type+'_succeed',0) + 1
            Newdict[node.node_type+'_not_succeed'] = Newdict.get(node.node_type+'_not_succeed',0) + 0
        else:
            Newdict[node.node_type+'_not_succeed'] = Newdict.get(node.node_type+'_not_succeed',0) + 1
            Newdict[node.node_type+'_succeed'] = Newdict.get(node.node_type+'_succeed',0) + 0
    return Newdict
    

In [33]:
from aiida.orm import CalcJobNode
from aiida.orm import QueryBuilder
qb = QueryBuilder()
qb.append(CalcJobNode)
CalcNode = qb.all()

exit_state,exit_message,index,exit_state_digit = GetCalNode()


ProcessState.FINISHED
3122
ProcessState.FINISHED
16631
ProcessState.FINISHED
93896
ProcessState.FINISHED
53194
ProcessState.FINISHED
16172
ProcessState.FINISHED
12498
ProcessState.FINISHED
132224
ProcessState.FINISHED
3201
ProcessState.FINISHED
139972
ProcessState.FINISHED
139849
ProcessState.FINISHED
139813
ProcessState.FINISHED
139724
ProcessState.FINISHED
137485
ProcessState.FINISHED
137465
ProcessState.FINISHED
135168
ProcessState.FINISHED
135151
ProcessState.FINISHED
135133
ProcessState.FINISHED
135073
ProcessState.FINISHED
138208
ProcessState.FINISHED
134900
ProcessState.FINISHED
134838
ProcessState.FINISHED
134754
ProcessState.FINISHED
134739
ProcessState.FINISHED
134724
ProcessState.FINISHED
134707
ProcessState.FINISHED
134690
ProcessState.FINISHED
138357
ProcessState.FINISHED
135340
ProcessState.FINISHED
135322
ProcessState.FINISHED
135216
ProcessState.FINISHED
133997
ProcessState.FINISHED
132144
ProcessState.FINISHED
132148
ProcessState.FINISHED
132160
ProcessState.FINISHED
1

ProcessState.EXCEPTED
137058
ProcessState.EXCEPTED
137050
ProcessState.EXCEPTED
137028
ProcessState.EXCEPTED
137026
ProcessState.EXCEPTED
137022
ProcessState.EXCEPTED
137000
ProcessState.FINISHED
139067
ProcessState.EXCEPTED
136999
ProcessState.EXCEPTED
136986
ProcessState.EXCEPTED
136980
ProcessState.EXCEPTED
136976
ProcessState.EXCEPTED
136961
ProcessState.EXCEPTED
136952
ProcessState.EXCEPTED
136939
ProcessState.FINISHED
139063
ProcessState.FINISHED
139059
ProcessState.EXCEPTED
136936
ProcessState.EXCEPTED
137363
ProcessState.EXCEPTED
137327
ProcessState.EXCEPTED
137313
ProcessState.EXCEPTED
137307
ProcessState.EXCEPTED
137287
ProcessState.EXCEPTED
137277
ProcessState.FINISHED
139055
ProcessState.FINISHED
139051
ProcessState.EXCEPTED
137270
ProcessState.EXCEPTED
137264
ProcessState.EXCEPTED
137257
ProcessState.EXCEPTED
137255
ProcessState.EXCEPTED
137224
ProcessState.EXCEPTED
137218
ProcessState.EXCEPTED
137188
ProcessState.FINISHED
139047
ProcessState.EXCEPTED
137187
ProcessState.E

ProcessState.FINISHED
134959
ProcessState.FINISHED
134931
ProcessState.FINISHED
134924
ProcessState.FINISHED
134915
ProcessState.FINISHED
134908
ProcessState.FINISHED
134893
ProcessState.FINISHED
134834
ProcessState.FINISHED
134830
ProcessState.FINISHED
134826
ProcessState.FINISHED
134822
ProcessState.FINISHED
134803
ProcessState.FINISHED
134802
ProcessState.FINISHED
134801
ProcessState.FINISHED
134800
ProcessState.FINISHED
134799
ProcessState.FINISHED
134747
ProcessState.FINISHED
134732
ProcessState.FINISHED
134717
ProcessState.FINISHED
134700
ProcessState.FINISHED
134683
ProcessState.FINISHED
134668
ProcessState.FINISHED
134654
ProcessState.FINISHED
134633
ProcessState.FINISHED
134625
ProcessState.FINISHED
134617
ProcessState.FINISHED
134604
ProcessState.FINISHED
134599
ProcessState.FINISHED
134594
ProcessState.FINISHED
134589
ProcessState.FINISHED
134584
ProcessState.FINISHED
134579
ProcessState.FINISHED
139005
ProcessState.FINISHED
139004
ProcessState.FINISHED
139003
ProcessState.F

ProcessState.EXCEPTED
25026
ProcessState.EXCEPTED
25025
ProcessState.EXCEPTED
25024
ProcessState.EXCEPTED
25023
ProcessState.EXCEPTED
25022
ProcessState.EXCEPTED
25021
ProcessState.EXCEPTED
25020
ProcessState.EXCEPTED
25019
ProcessState.EXCEPTED
25018
ProcessState.EXCEPTED
25129
ProcessState.EXCEPTED
25033
ProcessState.EXCEPTED
25032
ProcessState.EXCEPTED
25128
ProcessState.EXCEPTED
25330
ProcessState.EXCEPTED
25329
ProcessState.EXCEPTED
25328
ProcessState.EXCEPTED
25327
ProcessState.EXCEPTED
25326
ProcessState.EXCEPTED
25325
ProcessState.EXCEPTED
25324
ProcessState.EXCEPTED
25323
ProcessState.EXCEPTED
25133
ProcessState.EXCEPTED
25132
ProcessState.EXCEPTED
25131
ProcessState.EXCEPTED
25130
ProcessState.EXCEPTED
25127
ProcessState.EXCEPTED
25126
ProcessState.EXCEPTED
25125
ProcessState.EXCEPTED
25124
ProcessState.EXCEPTED
25123
ProcessState.EXCEPTED
25122
ProcessState.EXCEPTED
25121
ProcessState.EXCEPTED
25120
ProcessState.EXCEPTED
25119
ProcessState.EXCEPTED
25118
ProcessState.EXCEPTE

ProcessState.EXCEPTED
21218
ProcessState.EXCEPTED
21211
ProcessState.EXCEPTED
21210
ProcessState.EXCEPTED
21203
ProcessState.EXCEPTED
21202
ProcessState.EXCEPTED
21195
ProcessState.EXCEPTED
21194
ProcessState.EXCEPTED
21184
ProcessState.EXCEPTED
21182
ProcessState.EXCEPTED
21169
ProcessState.EXCEPTED
21168
ProcessState.EXCEPTED
21157
ProcessState.EXCEPTED
21153
ProcessState.EXCEPTED
21141
ProcessState.EXCEPTED
21140
ProcessState.EXCEPTED
21127
ProcessState.EXCEPTED
21125
ProcessState.EXCEPTED
21113
ProcessState.EXCEPTED
21112
ProcessState.EXCEPTED
21100
ProcessState.EXCEPTED
25322
ProcessState.EXCEPTED
25321
ProcessState.EXCEPTED
25320
ProcessState.EXCEPTED
25319
ProcessState.EXCEPTED
25318
ProcessState.EXCEPTED
24521
ProcessState.EXCEPTED
24520
ProcessState.EXCEPTED
24517
ProcessState.EXCEPTED
24516
ProcessState.EXCEPTED
24515
ProcessState.EXCEPTED
24513
ProcessState.EXCEPTED
24511
ProcessState.EXCEPTED
24510
ProcessState.EXCEPTED
24507
ProcessState.EXCEPTED
24500
ProcessState.EXCEPTE

...

ProcessState.FINISHED
61486
ProcessState.FINISHED
61488
ProcessState.FINISHED
61489
ProcessState.FINISHED
61491
ProcessState.EXCEPTED
125269
ProcessState.FINISHED
61493
ProcessState.FINISHED
61495
ProcessState.FINISHED
61496
ProcessState.FINISHED
61498
ProcessState.FINISHED
61499
ProcessState.FINISHED
61500
ProcessState.EXCEPTED
125277
ProcessState.FINISHED
61501
ProcessState.FINISHED
61502
ProcessState.FINISHED
61503
ProcessState.FINISHED
61504
ProcessState.FINISHED
61505
ProcessState.FINISHED
61506
ProcessState.EXCEPTED
125285
ProcessState.FINISHED
61507
ProcessState.FINISHED
61510
ProcessState.FINISHED
61511
ProcessState.FINISHED
61515
ProcessState.FINISHED
61516
ProcessState.FINISHED
68450
ProcessState.EXCEPTED
84509
ProcessState.FINISHED
68457
ProcessState.FINISHED
68463
ProcessState.FINISHED
65233
ProcessState.FINISHED
61205
ProcessState.FINISHED
61210
ProcessState.FINISHED
61217
ProcessState.EXCEPTED
84510
ProcessState.FINISHED
61222
ProcessState.FINISHED
61224
ProcessState.FINI

ProcessState.FINISHED
90037
ProcessState.FINISHED
90044
ProcessState.EXCEPTED
84580
ProcessState.FINISHED
91363
ProcessState.FINISHED
89814
ProcessState.FINISHED
91376
ProcessState.FINISHED
97758
ProcessState.FINISHED
97774
ProcessState.FINISHED
97788
ProcessState.FINISHED
97797
ProcessState.FINISHED
97811
ProcessState.FINISHED
97823
ProcessState.FINISHED
97824
ProcessState.FINISHED
97836
ProcessState.FINISHED
98084
ProcessState.FINISHED
61149
ProcessState.FINISHED
61150
ProcessState.FINISHED
61151
ProcessState.FINISHED
61152
ProcessState.FINISHED
61153
ProcessState.FINISHED
61154
ProcessState.EXCEPTED
83587
ProcessState.FINISHED
61155
ProcessState.FINISHED
68553
ProcessState.FINISHED
80161
ProcessState.FINISHED
80165
ProcessState.FINISHED
80169
ProcessState.FINISHED
80173
ProcessState.FINISHED
78800
ProcessState.FINISHED
126237
ProcessState.FINISHED
79278
ProcessState.FINISHED
82139
ProcessState.FINISHED
79246
ProcessState.FINISHED
80264
ProcessState.FINISHED
80265
ProcessState.FINISH

ProcessState.FINISHED
79840
ProcessState.FINISHED
79841
ProcessState.FINISHED
79842
ProcessState.FINISHED
79852
ProcessState.FINISHED
70295
ProcessState.FINISHED
70296
ProcessState.FINISHED
125753
ProcessState.FINISHED
125760
ProcessState.FINISHED
125768
ProcessState.FINISHED
125776
ProcessState.FINISHED
70298
ProcessState.FINISHED
65279
ProcessState.FINISHED
65284
ProcessState.FINISHED
65288
ProcessState.FINISHED
65290
ProcessState.FINISHED
65293
ProcessState.FINISHED
65294
ProcessState.FINISHED
65298
ProcessState.FINISHED
65299
ProcessState.FINISHED
65303
ProcessState.EXCEPTED
84273
ProcessState.FINISHED
65304
ProcessState.FINISHED
65307
ProcessState.FINISHED
65309
ProcessState.FINISHED
65313
ProcessState.FINISHED
65314
ProcessState.FINISHED
65318
ProcessState.EXCEPTED
84281
ProcessState.FINISHED
65320
ProcessState.FINISHED
65323
ProcessState.FINISHED
65326
ProcessState.FINISHED
65328
ProcessState.FINISHED
65331
ProcessState.FINISHED
65333
ProcessState.EXCEPTED
84291
ProcessState.FIN

ProcessState.EXCEPTED
131919
ProcessState.EXCEPTED
131927
ProcessState.EXCEPTED
131931
ProcessState.EXCEPTED
131935
ProcessState.EXCEPTED
131942
ProcessState.EXCEPTED
131963
ProcessState.EXCEPTED
131967
ProcessState.EXCEPTED
131971
ProcessState.EXCEPTED
10483
ProcessState.EXCEPTED
10484
ProcessState.EXCEPTED
10491
ProcessState.EXCEPTED
92397
ProcessState.EXCEPTED
10492
ProcessState.EXCEPTED
10498
ProcessState.EXCEPTED
10502
ProcessState.EXCEPTED
10402
ProcessState.EXCEPTED
10417
ProcessState.EXCEPTED
10418
ProcessState.EXCEPTED
10427
ProcessState.FINISHED
131751
ProcessState.FINISHED
131756
ProcessState.FINISHED
131760
ProcessState.FINISHED
131764
ProcessState.FINISHED
131768
ProcessState.FINISHED
131951
ProcessState.EXCEPTED
130932
ProcessState.EXCEPTED
103543
ProcessState.EXCEPTED
130936
ProcessState.EXCEPTED
130940
ProcessState.EXCEPTED
130944
ProcessState.EXCEPTED
130948
ProcessState.EXCEPTED
130952
ProcessState.EXCEPTED
130956
ProcessState.EXCEPTED
103552
ProcessState.EXCEPTED
130

ProcessState.FINISHED
75213
ProcessState.FINISHED
75224
ProcessState.FINISHED
75242
ProcessState.FINISHED
75253
ProcessState.FINISHED
75262
ProcessState.FINISHED
75275
ProcessState.FINISHED
75280
ProcessState.FINISHED
75305
ProcessState.FINISHED
75316
ProcessState.FINISHED
75317
ProcessState.FINISHED
75327
ProcessState.FINISHED
75331
ProcessState.FINISHED
75332
ProcessState.FINISHED
75342
ProcessState.FINISHED
75350
ProcessState.FINISHED
75383
ProcessState.FINISHED
75384
ProcessState.FINISHED
75388
ProcessState.FINISHED
75392
ProcessState.FINISHED
75396
ProcessState.FINISHED
75400
ProcessState.FINISHED
75404
ProcessState.FINISHED
65610
ProcessState.FINISHED
65611
ProcessState.FINISHED
65612
ProcessState.FINISHED
65613
ProcessState.FINISHED
65629
ProcessState.FINISHED
65636
ProcessState.FINISHED
65637
ProcessState.FINISHED
65638
ProcessState.FINISHED
66304
ProcessState.FINISHED
66313
ProcessState.FINISHED
66321
ProcessState.FINISHED
66416
ProcessState.FINISHED
66422
ProcessState.FINISHE

In [34]:
ShowCalNode(exit_state,exit_message,index,exit_state_digit)

ValueError: Requested 16298 colors, function can only return colors up to the base palette's length (256)

In [35]:
Newdict1 = GetWorkflowNode(WorkflowNode)
Newdict2 = GetWorkflowNode(CalcJobNode)
print(Newdict1)
print(Newdict2)

NameError: name 'WorkflowNode' is not defined

In [36]:
def ShowWorkflow(WorkflowDict):
    from bokeh.io import output_file, show
    from bokeh.models import ColumnDataSource,HoverTool
    from bokeh.plotting import figure
    from bokeh.io import output_notebook
    from bokeh.palettes import inferno

    output_file("ShowingCal.html")

    index = list(WorkflowDict.keys())
    counts = list(WorkflowDict.values())
    #exit_message = exit_message
    #exit_state_string = exit_state
    #exit_state_digit = exit_state_digit
      
    source = ColumnDataSource(data=dict(index=index, counts=counts, color=inferno(len(index))))
    
    TOOLTIPS = [
    ("Node number", "@counts"),
    ("(x,y)", "($x, $y)"),
    ("Node status", "@index"),   
    ]
   
    HT = HoverTool(
    tooltips=TOOLTIPS,

    mode='vline'
    )
    
    p = figure( y_range=(0,50), x_range=index, plot_width=800, plot_height=800, title="Process Node Information",tools = [HoverTool(mode='vline')],tooltips=TOOLTIPS)
    #print('step figure done')
    p.vbar(x="index", top="counts", bottom=0, width=1, color='color',  source=source)
    #print('step hbar done')
    
    output_notebook()
    p.xgrid.grid_line_color = None
    #p.legend = False
    show(p)

ShowWorkflow(Newdict1)
ShowWorkflow(Newdict2)

NameError: name 'Newdict1' is not defined

# SubtaskD1.i: Provenance

Task: Database and provenance health: display the number of nodes who have no incomming and outgoing links, no incomming links (any number outgoing), and no outgoing links (any number incomming)

In [39]:
def Count_In_Out():
    from aiida.orm import QueryBuilder
    qb = QueryBuilder()
    qb.append(Node)
    Nodes = qb.all()
    Namelist = ['No_Incoming','No_Outgoing','No_In&Out']

    Mydict = {}
    for n, in Nodes:
        Incoming_flag,Outgoingflag = False,False
        if(n.get_incoming().all_nodes() == []):
            Incoming_flag = True
            Mydict[Namelist[0]] = Mydict.get(Namelist[0],0)+1
        if(n.get_outgoing().all_nodes() == []):
            Outgoingflag = True
            Mydict[Namelist[1]] = Mydict.get(Namelist[1],0)+1
        if(Incoming_flag and Outgoingflag):
            Mydict[Namelist[2]] = Mydict.get(Namelist[2],0)+1

    return Mydict

def Show_In_Out(Mydict):
    from bokeh.io import output_file, show
    from bokeh.models import ColumnDataSource,HoverTool
    from bokeh.plotting import figure
    from bokeh.io import output_notebook
    from bokeh.palettes import Category20

    output_file("Show_In_Out.html")

    index = list(Mydict.keys())
    counts = list(Mydict.values())
      
    source = ColumnDataSource(data=dict(index=index, counts=counts, color=Category20[len(index)]))
    
    TOOLTIPS = [
    ("Node number", "@counts"),
    ("(x,y)", "($x, $y)"),
    ("Node status", "@index"),   
    ]
   
    HT = HoverTool(
    tooltips=TOOLTIPS,

    mode='vline'
    )
    
    p = figure( y_range=(0,6000), x_range=index, plot_width=800, plot_height=800, title="CalcNode Information",tools = [HoverTool(mode='vline')],tooltips=TOOLTIPS)
    #print('step figure done')
    p.vbar(x="index", top="counts", bottom=0, width=1, color='color',  source=source)
    #print('step hbar done')
    
    output_notebook()
    p.xgrid.grid_line_color = None
    #p.legend = False
    show(p)

In [ ]:
Mydict = Count_In_Out()
print(Mydict)

In [ ]:
Show_In_Out(Mydict)